In [2]:
%load_ext autoreload
%autoreload 2



In [36]:
import pandas as pd
from lyrics import search_artist_on_spotify, search_song_on_spotify, search_lyrics_on_genius, scrape_lyrics
import time
import os


In [4]:
df = pd.read_csv("../data/ver1_updated.csv")

In [5]:
df.head()

Unnamed: 0              spotify_id  ...  speechiness  release_date
0           0  65UgeS6VdIpUQqR3UoGw9j  ...       0.0622           NaN
1           1  71BqAINEnezjQfxE4VuJfq  ...       0.0550           NaN
2           2  5fp7tsbfsLW8ueAqrvcXOM  ...       0.2470           NaN
3           3  5YLfD5P6wnlAtKG6l4kObB  ...       0.1610           NaN
4           4  3Ei2OxIID6rSuPkvp6dIGP  ...       0.1430           NaN

[5 rows x 39 columns]

In [6]:
df.columns

Index(['Unnamed: 0', 'spotify_id', 'daily_rank', 'popularity', 'is_explicit',
       'duration_ms', 'album_name', 'album_release_date', 'time_signature',
       'rank', 'artists_num', 'artist_individual', 'artist_id', 'artist_genre',
       'album_num_tracks', 'weeks_on_chart', 'duration', 'region', 'language',
       'track_name', 'artist_names', 'country', 'loudness', 'tempo',
       'artist_count_df1', 'bpm_df1', 'artist_count_df2', 'streams', 'bpm_df2',
       'key', 'mode', 'danceability', 'valence', 'energy', 'acousticness',
       'instrumentalness', 'liveness', 'speechiness', 'release_date'],
      dtype='object')

In [7]:
df.shape

(25199, 39)

In [9]:
song_name = "Die with a smile"
artist_name = "Lady Gaga, Bruno Mars"
search_lyrics_on_genius(song_name, artist_name)

{'meta': {'status': 200}, 'response': {'hits': [{'highlights': [], 'index': 'song', 'type': 'song', 'result': {'annotation_count': 2, 'api_path': '/songs/10766684', 'artist_names': 'Lady Gaga & Bruno Mars', 'full_title': 'Die With A Smile by\xa0Lady\xa0Gaga & Bruno\xa0Mars', 'header_image_thumbnail_url': 'https://images.genius.com/abe185baf2b9fd84ebb5d493ffe715b3.300x300x1.png', 'header_image_url': 'https://images.genius.com/abe185baf2b9fd84ebb5d493ffe715b3.1000x1000x1.png', 'id': 10766684, 'lyrics_owner_id': 8280771, 'lyrics_state': 'complete', 'path': '/Lady-gaga-and-bruno-mars-die-with-a-smile-lyrics', 'primary_artist_names': 'Lady Gaga & Bruno Mars', 'pyongs_count': 31, 'relationships_index_url': 'https://genius.com/Lady-gaga-and-bruno-mars-die-with-a-smile-sample', 'release_date_components': {'year': 2024, 'month': 8, 'day': 16}, 'release_date_for_display': 'August 16, 2024', 'release_date_with_abbreviated_month_for_display': 'Aug. 16, 2024', 'song_art_image_thumbnail_url': 'https

(True,
 'https://genius.com/Lady-gaga-and-bruno-mars-die-with-a-smile-lyrics',
 'Lady Gaga',
 ['Bruno Mars'],
 'August 16, 2024')

In [5]:
df["has_lyrics"] = False
df["lyrics_url"] = None
df["lyrics"] = None
df["scraped"] = False
df["primary_artist"] = None
df["feat_artist"] = None # string separated by comma


In [25]:
for row in df[400:800].itertuples(index=True):  # Set index=True if you need the index
    print(f"{row.Index}, {row.track_name}, {row.artist_names}")
    is_found, lyric_url, primary_artist, feat_artists, release_date = search_lyrics_on_genius(song_name=row.track_name, artist_name=row.artist_names)
    df.loc[row.Index, "has_lyrics"] = is_found
    df.loc[row.Index, "lyric_url"] = lyric_url
    df.loc[row.Index, "primary_artist"] = primary_artist
    df.loc[row.Index, "feat_artist"] = feat_artists
    df.loc[row.Index, "release_date"] = release_date
    
    if is_found:
        lyrics = scrape_lyrics(lyrics_url=lyric_url)
        print(lyrics)
        df.loc[row.Index, "lyrics"] = lyrics
        df.loc[row.Index, "scraped"] = True

400, 4 Da Gang (with Roddy Ricch), 42 Dugg, Roddy Ricch
{'meta': {'status': 200}, 'response': {'hits': [{'highlights': [], 'index': 'song', 'type': 'song', 'result': {'annotation_count': 40, 'api_path': '/songs/6655820', 'artist_names': '42 Dugg & Roddy Ricch', 'full_title': '4 Da Gang by\xa042\xa0Dugg & Roddy\xa0Ricch', 'header_image_thumbnail_url': 'https://images.genius.com/a60d2266bd72ad05142756c0b24106a4.300x300x1.png', 'header_image_url': 'https://images.genius.com/a60d2266bd72ad05142756c0b24106a4.1000x1000x1.png', 'id': 6655820, 'lyrics_owner_id': 5748418, 'lyrics_state': 'complete', 'path': '/42-dugg-and-roddy-ricch-4-da-gang-lyrics', 'primary_artist_names': '42 Dugg & Roddy Ricch', 'pyongs_count': 22, 'relationships_index_url': 'https://genius.com/42-dugg-and-roddy-ricch-4-da-gang-sample', 'release_date_components': {'year': 2021, 'month': 4, 'day': 2}, 'release_date_for_display': 'April 2, 2021', 'release_date_with_abbreviated_month_for_display': 'Apr. 2, 2021', 'song_art_ima

In [26]:
count = df[0:800]["scraped"].sum()
print(f"scraped songs: {count}")

scraped songs: 374


In [27]:
df.to_pickle("../data/lyrics_800.pkl")

In [28]:
length = df.shape[0]
print(length)

25199


In [82]:
for i in range(11100, 11400, 100):
    for row in df[i:i+100].itertuples(index=True):  # Set index=True if you need the index
        
        print(f"{row.Index}, {row.track_name}, {row.artist_names}")
        is_found, lyric_url, primary_artist, feat_artists, release_date = search_lyrics_on_genius(song_name=row.track_name, artist_name=row.artist_names)
        df.loc[row.Index, "has_lyrics"] = is_found
        df.loc[row.Index, "lyric_url"] = lyric_url
        df.loc[row.Index, "primary_artist"] = primary_artist
        df.loc[row.Index, "feat_artist"] = feat_artists
        df.loc[row.Index, "release_date"] = release_date
        if is_found:
            lyrics = scrape_lyrics(lyrics_url=lyric_url)
            df.loc[row.Index, "lyrics"] = lyrics
            df.loc[row.Index, "scraped"] = True
    filename = f"../data/lyrics_{i+100}.pkl"
    df.to_pickle(filename)
    to_delete = f"../data/lyrics_{i-200}.pkl"
    if os.path.exists(to_delete):
        os.remove(to_delete)
    
    time.sleep(60)
        

11100, Liability, Drake
11101, Liar, Silia Kapsis
11102, Liars, Half Deezy, DT The Artist, Boosie Badazz
11103, Liberta, Block 93, Yanek, Sp93, Tanto
11104, Liberte-Me, Juninho Vitório
11105, Licor 43, KayBlack, AMUSIK, Wall Hein
11106, Licorice, aespa
11107, Lidmašīnas, Prāta Vētra
11108, Lidojam tik augstu, Deniss, Sudrabu Sirds
11109, Lidokain, BSW, ByeAlex és a Slepp
11110, Lidt Længere (feat. Emil Kruse), KIDD, Emil Kruse
11111, Lie, BTS
11112, Lie, Kizz Daniel
11113, Lie To Girls, Sabrina Carpenter
11114, Lie With You, TEN
11115, Lieb mich, AYLIVA
11116, Lieb mich, AYLIVA
11117, Liebe Grüsse, RAF Camora, Ski Aggu
11118, Liebe Grüsse, RAF Camora, Ski Aggu
11119, Liebe in Stereo, Baby B3ns, Yung Hurn
11120, Liebe ist ein Dieb, Kontra K
11121, Lied 2 Me, Lokolil
11122, Lied To, One Mojo, Sik Jagga
11123, Lies Lies Lies, Morgan Wallen
11124, Lifa af, BRÍET, Birnir
11125, Life, Thamarvel
11126, Life Again, Annika Wickihalder
11127, Life Dey Go On, Brymo
11128, Life Goes On, BTS
11129,

KeyboardInterrupt: 

In [68]:
df_updated = pd.read_pickle("../data/lyrics_8500.pkl")
df_updated.head(10)

Unnamed: 0              spotify_id  daily_rank  popularity is_explicit  \
0           0  65UgeS6VdIpUQqR3UoGw9j        48.0        54.0       False   
1           1  71BqAINEnezjQfxE4VuJfq        41.0        91.0       False   
2           2  5fp7tsbfsLW8ueAqrvcXOM        41.0        12.0        True   
3           3  5YLfD5P6wnlAtKG6l4kObB        19.0        47.0        True   
4           4  3Ei2OxIID6rSuPkvp6dIGP        49.0        57.0        True   
5           5  3bY8hZbtWQpCOGHi1IZvz5        47.0        39.0       False   
6           6  68cUJFq7aAbgeurngTmngL        50.0        82.0        True   
7           7  2uGrSoj2G2ttrcGvDSl5Bg        50.0        42.0       False   
8           8  44muA7zBeipDRXs1uaTNLv        31.0        68.0       False   
9           9  1DNXCTUHCGcr9kJ6LynYEC        47.0        50.0       False   

   duration_ms                   album_name album_release_date  \
0     145511.0                         "Se"         2024-01-19   
1     180381.0      1989 (Taylor's Version)         2023-10-26   
2     183003.0                     BENIHANA         2024-03-15   
3     129522.0                            X         2024-03-03   
4     178775.0              #PHONKFREESTYLE         2024-01-26   
5     195818.0         #Sarkanbaltsarkanais         2019-11-13   
6     208898.0           $AD BOYZ 4 LIFE II         2023-10-05   
7     175813.0  PRODUCE 101 JAPAN THE GIRLS         2023-12-18   
8     175813.0          35 GIRLS 5 CONCEPTS         2023-12-01   
9     250595.0             a beautiful blur         2023-09-29   

   time_signature  rank  ...  liveness speechiness        release_date  \
0             4.0   NaN  ...    0.1350      0.0622                None   
1             4.0   NaN  ...    0.0603      0.0550                None   
2             4.0   NaN  ...    0.1060      0.2470                None   
3             4.0   NaN  ...    0.1110      0.1610       March 3, 2024   
4             4.0   NaN  ...    0.1280      0.1430    January 26, 2024   
5             4.0   NaN  ...    0.4030      0.1040    October 13, 2019   
6             3.0   NaN  ...    0.1740      0.0592     October 5, 2023   
7             4.0   NaN  ...    0.3060      0.0969                None   
8             4.0   NaN  ...    0.3010      0.1040                None   
9             3.0   NaN  ...    0.1240      0.0338  September 29, 2023   

  has_lyrics  lyrics_url                                             lyrics  \
0      False        None                                               None   
1      False        None                                               None   
2      False        None                                               None   
3       True        None  [Parole de "#BÂTIMENT1"]\n[Refrain]\nÉloigné d...   
4       True        None  ["#PHONKFREESTYLE" için şarkı sözleri]\n[Giriş...   
5       True        None  Sarkan balt sarkanais mastā plīvo\nRedzi te le...   
6       True        None  [Letra de "$AD BOYZ II"]\n[Verso]\nBaby, recue...   
7      False        None                                               None   
8      False        None                                               None   
9       True        None  [Verse 1]\nChasin' a heart is like chasin' a g...   

   scraped     primary_artist                   feat_artist  \
0    False               None                          None   
1    False               None                          None   
2    False               None                          None   
3     True            Tiakola                                 
4     True          DEHA INC.  Şehinşah, Reckol, 13 Killoki   
5     True  Bermudu Divstūris                                 
6     True           Junior H                                 
7    False               None                          None   
8    False               None                          None   
9     True               LANY                                 

                                           lyric_

In [85]:
df_done = pd.read_pickle("../data/lyrics_25200.pkl")
df_done.shape

(25199, 46)

In [115]:
df_done.to_csv("../data/lyrics_duplicates_removed.csv")

In [86]:
df_done = df_done.drop_duplicates(subset=['track_name'], keep='first')

In [87]:
df_done.shape

(21622, 46)

In [112]:
df_slice = df_done[-400:-200].copy()  # Explicitly create a copy
df_slice['language'] = "Non-English"  # Modify the copy
df_done.update(df_slice)